In [34]:
# imports and settings
from distutils.dir_util import copy_tree
import os
import sys
sys.path.insert(0, '../functions/')
import interface_GAMS as iG
import parameter_optimization as po
import multiprocessing
import numpy as np
import pickle
import pandas as pd
from itertools import product
import concurrent.futures
import platform
import shutil
import math
from multiprocessing import Pool
import warnings
warnings.filterwarnings("ignore", category=UserWarning)

# settings
testing = True
small_dataset = True # only use the first 50 samples, mostly useful when using a limited license
pull_best_paras = True
loop_total = 3  # let's start with 10 loops
cases_run = [] # only run these particular cases


# below are the default flags used if nothing is pre-set
# set flags by editing the "saved_flags.csv" in the ../data folder
t_half_life_deg = 300
stable_flags = { # these do not change gene by gene
    # overall
    'only_create_ratios' : False,
    'only_check_KdRNAPAct' : False, # if True, quit out of code after generating KdRNAPAct, done to see if it is generating valid values through sanity check plots
    'include_Amy_samples' : True, # append on Amy's stationary phase samples to analysis
    'remove_outliers' : True, # removes samples that do not correlate well with others, see ../data_cleaning/1_locate_outliers_to_drop.ipynb
    'drop_basal_conds' : True, # if True, removes basal conditions from sample after they're used to calculate ratios (useful when their outliers)

    # KdRNAPAct optimization
    'KdRNAPAct_sanity' : True, # if True, return sanity plots from this optimization
    
    # GAMs
    'limit_TF_conc_by_actual' : False, # limits the TF concentrations for the model by the actual values, otherwise lets it be a very wide range
    'supress_output' : False,
    'use_greedy' : True, # use the greedy algo values (if False, uses the results of the GA)
    'run_on_all' : False, # run on all genes that are in the saved output folder
    'limit_samples' : [], # if run_on_all is False, limit to these samples (or which of them are available)
    'delete_old' : True,
    'run_seperate' : False, # run cActivator and cInhibitor solvers seperately
    
    # input constants for GAMs (all get logged inside GAMs so pass in un-logged)
    'act_TF_conc_lo' : 2.902870141566294e-13 / 100, # minimum TF conc found in Heineman data
    'act_TF_conc_up' : 0.00014190659526601638 * 100, # max of ^
    'inh_TF_conc_lo' : 2.902870141566294e-13 / 100, # minimum TF conc found in Heineman data
    'inh_TF_conc_up' : 0.00014190659526601638 * 100, # max of ^
    'inh_metab_Total_lo' : 0.000038 / 1000000000, # minimum of arginine concentration in stationary phase samples, div a buffer
    'inh_metab_Total_up' : 0.000408 * 1000000000, # maximum of arginine concentration in stationary phase samples, mult a buffer
    'act_metab_Total_lo' : 0.000038 / 1000000000, # minimum of arginine concentration in stationary phase samples, div a buffer
    'act_metab_Total_up' : 0.000408 * 1000000000, # maximum of arginine concentration in stationary phase samples, mult a buffer

    
    # GAMS results
    'act_Kd_lo' : 1.697190518937953e-09,
    'act_Kd_up' : 56221.67194139278,
    'inh_Kd_lo' : 1.697190518937953e-09, 
    'inh_Kd_up' : 56221.67194139278,
    'weight_act_obj1' : 8.192636589173368,
    'weight_inh_obj1' : 8.192636589173368,
    'weight_mRNA_match' :  3.749702173312575e-05,    
    
    
    # misc
    'eq_str' : 'Eq(mRNARatio,((cActivator*KdRNAP + KdRNAPAct)*(KdRNAP + RNAP + \
            KeqOpening*RNAP))/((1 + cActivator + cInhibitor)*KdRNAP*KdRNAPAct + \
            cActivator*KdRNAP*(1 + KeqOpening)*RNAP + KdRNAPAct*(1 + \
            KeqOpening)*RNAP))',
    
    # cell_constants'
    'cell_constants_RNAP': 10**-6,
    'cell_constants_mRNA_total': 1800, # Total mRNA/cell from https://www.ncbi.nlm.nih.gov/pmc/articles/PMC3554401
    'cell_constants_cell_volume': 10**-15, # Liters from https://bionumbers.hms.harvard.edu/bionumber.aspx?id=100004&ver=19
    'cell_constants_kDeg': np.log(2)/t_half_life_deg, # Rate of degradation
    'cell_constants_promoterConcVal': 10**-9, # Promoter concentration
    'cell_constants_u': 1/3600, # Growth rategit s
}
stable_flags.update({'small_dataset' : small_dataset})

# load in settings flags
if testing:
    flags_filepath = '../options/test_gene_flags.csv'
    TF_flags_filepath = '../options/test_TF_flags.csv'
else:
    flags_filepath = '../options/gene_flags.csv'
    TF_flags_filepath = '../options/TF_flags.csv'
flags_df = pd.read_csv(flags_filepath, index_col = 0)
flags_df = pd.read_csv(flags_filepath, index_col = 0)
flags_df = flags_df[flags_df['include'] == True]

all_paras = ['act_metab_Total_lo', 'act_metab_Total_up',
             'inh_metab_Total_lo', 'inh_metab_Total_up',
             'act_Kd_lo', 'act_Kd_up',
             'inh_Kd_lo', 'inh_Kd_up',
             'act_TF_conc_lo', 'act_TF_conc_up',
             'inh_TF_conc_lo', 'inh_TF_conc_up',
             'weight_act_obj1', 'weight_inh_obj1', 'weight_mRNA_match']

def show_figure(fig):

    # create a dummy figure and use its
    # manager to display "fig"

    dummy = plt.figure()
    new_manager = dummy.canvas.manager
    new_manager.canvas.figure = fig
    fig.set_canvas(new_manager.canvas)

# runs over all cases to optimize parameter limits

In [35]:
# run

# constants
cell_constants = {
    'RNAP' : stable_flags['cell_constants_RNAP'],
    'mRNA_total' : stable_flags['cell_constants_mRNA_total'],
    'cell_volume' : stable_flags['cell_constants_cell_volume'],
    'kDeg' : stable_flags['cell_constants_kDeg'],
    'promoterConcVal' : stable_flags['cell_constants_promoterConcVal'],
}


def mask_func(inp0, inp1, inp2, inp3, inp4, inp5):
    if os.path.exists(inp4):
        shutil.rmtree(inp4, ignore_errors = True)
    os.mkdir(inp4)
    os.mkdir(inp4+'/input_files')
    os.mkdir(inp4+'/output_files')
    os.mkdir(inp4+'/input_GDX')
    os.mkdir(inp4+'/output_GDX')
    iG.run_multi_GAMS(inp0, inp1, inp2, inp3, inp4, parameter_flags = inp5)


# collect and sort all cases
flags_df = pd.read_csv(flags_filepath, index_col = 0)
flags_df = flags_df[flags_df['include']]
n_range = 3 # hard set to this now, but some other variables use it
if len(cases_run) == 0:
    all_cases = list(set([(str(row['act_iM']), str(row['inh_iM'])) for _, row in flags_df.iterrows()]))
    all_cases.sort(key = lambda k : str(k[0]))
    all_cases.sort(key = lambda k : str(k[1]))
else:
    all_cases = list(set([(str(case.split('___')[0]), str(case.split('___')[1])) for case in cases_run]))
    all_cases.sort(key = lambda k : str(k[0]))
    all_cases.sort(key = lambda k : str(k[1]))
TF_flags_df = pd.read_csv(TF_flags_filepath, index_col = 0)
prev_add_back = False
for case_iMs in all_cases: # let's get it to work once first
    # convert to cases
    case = (str(case_iMs[0])+'__'+str(case_iMs[1])).replace('/', '_').replace(' ', '_')
    #cases = [case for case in cases if str(case) != 'nan']
    # quit out early if filtering runs
    #case = '___'.join(list(cases)).replace(' ', '_').replace('/', '_')
    
    # load in 
    if os.path.exists('../GAMS/optimization_runs/'+case+'/iter_to_best_run_info.pkl'):
        pickle_in = open('../GAMS/optimization_runs/'+case+'/iter_to_best_run_info.pkl', 'rb')
        iter_to_best_run_info = pickle.load(pickle_in)
        pickle_in.close()
    else:
        iter_to_best_run_info = {}

    # limit down dataframes to relevant
    case_iMs = (case_iMs[0].replace('_', '/'), case_iMs[1].replace('_', '/'))
    cases = [case.replace('_', '/') for case in case_iMs if str(case) != 'nan']
    bby_TF_flags_df = TF_flags_df.loc[cases]
    bby_flags_df = flags_df[(flags_df['act_iM'] == case_iMs[0]) | (case_iMs[0] == 'nan' and flags_df['act_iM'].isna())]
    bby_flags_df = bby_flags_df[(bby_flags_df['inh_iM'] == case_iMs[1]) | (case_iMs[1] == 'nan' and bby_flags_df['inh_iM'].isna())]
    stable_flags.update({'limit_samples' : bby_flags_df.index.to_list()})
    
     # we need to include certain sweep_paras based on case selected
    bby_TF = TF_flags_df.loc[cases].sum()
    sweep_paras = set(['weight_mRNA_match'])
    if bby_TF['cAct_no_effector_form'] != 0:
        for para in ['act_Kd_lo', 'act_Kd_up', 'act_TF_conc_lo', 'act_TF_conc_up']:
            sweep_paras.add(para)
    if bby_TF['cAct_multi_effector_binding'] != 0:
        for para in ['act_Kd_lo', 'act_Kd_up']: # also metabolite kd, but I'm trying to not adjust that right now
            sweep_paras.add(para)
    if bby_TF['cAct_multi_co_effector_binding'] != 0:
        for para in ['act_Kd_lo', 'act_Kd_up']: # also metabolite kd, but I'm trying to not adjust that right now
            sweep_paras.add(para)
    if bby_TF['cInh_no_effector_form'] != 0:
        for para in ['act_Kd_lo', 'act_Kd_up', 'act_TF_conc_lo', 'act_TF_conc_up']:
            sweep_paras.add(para)
    if bby_TF['cInh_multi_effector_binding'] != 0:
        for para in ['act_Kd_lo', 'act_Kd_up']: # also metabolite kd, but I'm trying to not adjust that right now
            sweep_paras.add(para)
    if bby_TF['cInh_multi_co_effector_binding'] != 0:
        for para in ['act_Kd_lo', 'act_Kd_up']: # also metabolite kd, but I'm trying to not adjust that right now
            sweep_paras.add(para)
    sweep_paras = list(sweep_paras)
    OG_sweep_paras = sweep_paras.copy()

    # first loop settings
    reduce_amt = 0.8 # reduces the change val each loop to "zoom in" on a good answer
    if len(iter_to_best_run_info) == 0:
        if pull_best_paras:
            if os.path.exists('../data/case_to_best_paras.pkl'):
                pickle_in = open('../data/case_to_best_paras.pkl', 'rb')
                case_to_best_paras = pickle.load(pickle_in)
                pickle_in.close()
            else:
                case_to_best_paras = {}
            if case in case_to_best_paras:
                best_paras = dict(case_to_best_paras[case].Value)
                starting_paras = dict(case_to_best_paras[case].Value)
            else:
                print('case not in case_to_best_paras, running with defaults')
                best_paras = stable_flags
                starting_paras = stable_flags
            iter_ct = 1
            change_val = 5
            starting_index = tuple([-1 for _ in range(len(sweep_paras))])
        else:
            iter_ct = 1
            starting_index = tuple([-1 for _ in range(len(sweep_paras))])
            best_paras = stable_flags
            starting_paras = stable_flags
            change_val = 5
    else:
        max_iter = max(iter_to_best_run_info.keys())
        iter_ct = max_iter + 1
        starting_index = iter_to_best_run_info[max_iter][0]
        best_paras = dict(pd.read_csv(iter_to_best_run_info[max_iter][2]+'/input_files/parameters.csv', index_col = 0))['Value']
        change_val = iter_to_best_run_info[max_iter][1] * reduce_amt
        starting_paras = stable_flags
        # often this is because I quit a run early, I should go ahead and delete the unfinished folder if it exists
        obsolete_path = iter_to_best_run_info[max_iter][-1].split('/run_')[0].split('iter_')[0]+'iter_'+str(max_iter+1)
        if os.path.exists(obsolete_path):
            shutil.rmtree(obsolete_path)
    
    add_back = []
    while iter_ct < loop_total:
        print(case+': working on iter_ct : '+str(iter_ct))

        ############################
        # Generate inputs
        ############################
        # let's try filtering out old sweep_paras if same
        lists = []
        para_to_list = {}
        for index, para in zip(starting_index, sweep_paras):
            if index == 1 and para not in add_back: # this means the ideal value was the center, to mix it up let's reduce its change some to find a more local minima
                #temp_change_val = (change_val / 2) + 1
                # remove from next loop to speed up process, move on
                add_back.append(para)
                list_ = [best_paras[para]]
                para_to_list.update({para : list_})
                lists.append(list_)
            else:
                temp_change_val = change_val + 1

                list_ = [best_paras[para] / temp_change_val, best_paras[para], temp_change_val * best_paras[para]]#np.linspace(best_paras[para] - change_val*best_paras[para], best_paras[para] + change_val*best_paras[para], n_range)
                para_to_list.update({para : list_})
                lists.append(list_)
        if not prev_add_back and len(add_back) == len(sweep_paras):
            # we have centered on (1, 1, 1, ...) starting paras, let's reduce change_val and just reset
            # setup for next loop
            prev_add_back = True
            change_val *= reduce_amt
            print('previous run on center, further reducing change_val and rerunning')
            print('next change_val : ', end = '')
            print(change_val)
            print()
            continue
        prev_add_back = False # prevents endless cycling in add_back
        
        add_back = [] # reset add_back
        combos = product(*lists)
        i = 0
        inputs = []
        i_to_index = {}
        if not os.path.exists('../GAMS/optimization_runs/'+case):
            os.mkdir('../GAMS/optimization_runs/'+case)
        if not os.path.exists('../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)):
            os.mkdir('../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct))
        for combo in list(combos):
            index_vals = []
            para_dict = {}
            for para, val in zip(sweep_paras, combo):
                if 'act_' in para:
                    para2 = para.replace('act_', 'inh_')
                elif 'inh_' in para:
                    para2 = para.replace('inh_', 'act_')
                else:
                    para2 = None
                para_dict.update({para : val})
                if para2:
                    para_dict.update({para2 : val})
                index_vals.append(list(para_to_list[para]).index(val))

            # round out the para_dict
            for para in all_paras:
                if para not in para_dict:
                    para_dict.update({para : starting_paras[para]})

            i_to_index.update({i : tuple(index_vals)})
            GAMs_run_dir = '../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)+'/run_'+str(i)
            inputs.append((bby_flags_df, bby_TF_flags_df, stable_flags, cell_constants, GAMs_run_dir, para_dict))
            i += 1
        pickle_out = open('../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)+'/i_to_index.pkl', 'wb')
        pickle.dump(i_to_index, pickle_out)
        pickle_out.close()
        index_to_i = {v : k for k, v in i_to_index.items()}

        
        ############################
        # Run GAMs
        ############################
        print('running GAMS '+str(len(inputs))+' times...')
        # change stdout so we don't spam with GAMS output
        if platform.system() != 'Windows':
            with Pool(processes = 8) as pool:
                results = pool.starmap(mask_func, inputs)
        else:
            with concurrent.futures.ThreadPoolExecutor(max_workers = 8) as executor:
                results = executor.map(lambda args: mask_func(*args), inputs)

        ############################
        # Read results
        ############################
        print('reading results...')
        size = (n_range,) * len(sweep_paras)
        saved_act_errs = np.full(size, 9e10)
        saved_inh_errs = np.full(size, 9e10)
        saved_mRNA_errs = np.full(size, 9e10)
        tiebreaker = np.full(size, 9e10)

        # load for loop
        GAMs_run_dir = '../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)+'/run_1'
        iM_saved_cActivators = pd.read_csv(GAMs_run_dir+'/input_files/composite_cAct_vals.csv', index_col = 0)
        iM_saved_cInhibitors = pd.read_csv(GAMs_run_dir+'/input_files/composite_cInh_vals.csv', index_col = 0)
        cAct_mapping = pd.read_csv(GAMs_run_dir+'/input_files/cAct_mapping.csv', index_col = 0)
        cInh_mapping = pd.read_csv(GAMs_run_dir+'/input_files/cInh_mapping.csv', index_col = 0)
        grid = pd.read_csv(GAMs_run_dir+'/input_files/grid_constants.csv', index_col = 0)
        ratios_df = pd.read_csv(GAMs_run_dir+'/input_files/actual_mRNA_ratio.csv', index_col = 0)

        for f in os.listdir('../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)):
            if 'run_' not in f: continue
            # read in data

            try:
                # The _ is mRNA_ratio_df, but the code is set up to work without it and I don't want to break things
                mRNA_df, GAMS_calc_cAct, cAct_kd_df, act_metab_df, _, GAMS_calc_cInh, cInh_kd_df, inh_metab_df, _ = iG.read_multi_GAMs('../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)+'/'+f)
            except:
                # usually means the parameters were bad, just set the error very high so it gets ignored
                index = i_to_index[int(f.split('_')[1])]
                saved_act_errs[index] = 9e10
                saved_inh_errs[index] = 9e10
                saved_mRNA_errs[index] = 9e10
                continue

            # need to loop through each iM to pull out values
            act_errs = []
            inh_errs = []
            mRNA_errs = []
            act_inh_iM_pairs = [(act, inh) for act, inh in zip(bby_flags_df.act_iM, bby_flags_df.inh_iM)]
            for act_iM, inh_iM in set(act_inh_iM_pairs):
                # check that they both exist
                if type(act_iM) == float:
                    act_iM = inh_iM # this will correctly pull zero values to fill in
                    disp_act_iM = 'None'
                elif type(inh_iM) == float:
                    inh_iM = act_iM
                    disp_inh_iM = 'None'

                # grab genes
                g1 = cAct_mapping[cAct_mapping[act_iM] != 0].index.to_list()
                g2 = cInh_mapping[cInh_mapping[inh_iM] != 0].index.to_list()
                genes = list(set(g1).union(g2))

                # load in for loop
                calc_cAct = GAMS_calc_cAct[genes]
                calc_cInh = GAMS_calc_cInh[genes]
                saved_cActivators = iM_saved_cActivators[iM_saved_cActivators['iM'] == act_iM].drop(columns = 'iM').loc[genes]
                saved_cInhibitors = iM_saved_cInhibitors[iM_saved_cInhibitors['iM'] == inh_iM].drop(columns = 'iM').loc[genes]
                saved_cActivators = saved_cActivators.T.loc[calc_cAct.index]
                saved_cInhibitors = saved_cInhibitors.T.loc[calc_cInh.index]

                # collect cAct/cInh correlations
                if False: # correlation values, which don't really improve things much
                    for gene in calc_cInh.columns:
                        act_corr = np.corrcoef(list(calc_cAct[gene].values), list(saved_cActivators[gene].values))[0, 1]
                        if math.isnan(act_corr):
                            act_corr = 0
                        inh_corr = np.corrcoef(list(calc_cInh[gene].values), list(saved_cInhibitors[gene].values))[0, 1]
                        if math.isnan(inh_corr):
                            inh_corr = 0
                        act_errs.append(act_corr)
                        inh_errs.append(inh_corr)
                for gene in calc_cInh.columns:
                    # scale error by max input (so all are out of 1)
                    max_input = max(saved_cActivators[gene].values)
                    if max_input == 0:
                        max_input = 1
                    input_vals = saved_cActivators[gene].values / max_input
                    calc_vals = calc_cAct[gene].values / max_input
                    err = sum([(calc - inp)**2 for (calc, inp) in zip(calc_vals, input_vals)])
                    act_errs.append(err)

                    # now for cInhibitor
                    max_input = max(saved_cInhibitors[gene].values)
                    if max_input == 0:
                        max_input = 1
                    input_vals = saved_cInhibitors[gene].values / max_input
                    calc_vals = calc_cInh[gene].values / max_input
                    err = sum([(calc - inp)**2 for (calc, inp) in zip(calc_vals, input_vals)])
                    inh_errs.append(err)

                # convert to mRNA, get error      
                actual_mRNAs = []
                for gene in calc_cAct.columns:
                    shared = list(set(calc_cAct.index).intersection(set(calc_cInh.index)).intersection(ratios_df.index[ratios_df[gene].notnull()]))
                    # calculate mRNA from GAMS results
                    recon_mRNA = []
                    for sample in shared:
                        recon_mRNA.append(mRNA_df[gene].loc[sample])

                    # pull actual mRNA ratio
                    actual_mRNA = ratios_df.loc[shared][gene].values.flatten()

                    # scale both my maximum of actual_mRNA
                    max_actual = max(actual_mRNA)
                    if max_actual == 0:
                        max_actual = 1
                    scaled_actual = actual_mRNA / max_actual
                    scaled_recon = recon_mRNA / max_actual
                    err = sum([(calc - inp)**2 for (calc, inp) in zip(scaled_actual, scaled_recon)])
                    mRNA_errs.append(err)

            act_err = np.mean(act_errs)
            inh_err = np.mean(inh_errs)
            mRNA_err = np.mean(mRNA_errs)

            # save values
            index = i_to_index[int(f.split('_')[1])]
            saved_act_errs[index] = act_err
            saved_inh_errs[index] = inh_err
            saved_mRNA_errs[index] = mRNA_err
            
            # tiebeaker - we want tighter parameters if possible, if two are equal pick one with tighter parameters
            total = 0
            pairs = [('act_metab_Total_lo', 'act_metab_Total_up'),
                     ('inh_metab_Total_lo', 'inh_metab_Total_up'),
                     ('act_Kd_lo', 'act_Kd_up'),
                     ('inh_Kd_lo', 'inh_Kd_up'),
                     ('act_TF_conc_lo', 'act_TF_conc_up'),
                     ('inh_TF_conc_lo', 'inh_TF_conc_up'),
            ]
            temp_paras_df = pd.read_csv('../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)+'/'+f+'/input_files/parameters.csv', index_col = 0)
            for low, high in pairs:
                total += temp_paras_df.loc[high].values[0] - temp_paras_df.loc[low].values[0]
            tiebreaker[index] = total


        ############################
        # save best result
        ############################
        tiebreaker = (tiebreaker - min(tiebreaker[tiebreaker != 0])) / 1000 # scale down tiebreaker, you just want it to to break ties nothing else
        combo = saved_act_errs + saved_inh_errs + saved_mRNA_errs + tiebreaker
        overall_best = np.unravel_index(np.argmin(combo, axis=None), np.shape(combo))
        GAMs_run_dir = '../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)+'/run_'+str(index_to_i[overall_best])
        params = pd.read_csv(GAMs_run_dir+'/input_files/parameters.csv', index_col = 0)
        print(overall_best)
        print(dict(params['Value']))
        print('Overall_score: '+str(combo[overall_best]))
        print('cAct_err: '+str(saved_act_errs[overall_best]))
        print('cInh_err: '+str(saved_inh_errs[overall_best]))
        print('mRNA_err: '+str(saved_mRNA_errs[overall_best]))
        print('\n')
        iter_to_best_run_info.update({iter_ct : (overall_best, change_val, GAMs_run_dir)})
        pickle_out = open('../GAMS/optimization_runs/'+case+'/iter_to_best_run_info.pkl', 'wb')
        pickle.dump(iter_to_best_run_info, pickle_out)
        pickle_out.close()
        pickle_out = open('../GAMS/optimization_runs/'+case+'/index_to_i.pkl', 'wb')
        pickle.dump(index_to_i, pickle_out)
        pickle_out.close()


        ############################
        # delete the rest to save space (no need to look at bad runs afterwards)
        ############################
        base_dir = '../GAMS/optimization_runs/'+case+'/iter_'+str(iter_ct)+'/'
        best_dir = 'run_'+str(index_to_i[overall_best])
        for f_dir in os.listdir(base_dir):
            if 'run_' not in f_dir:
                continue
            if f_dir == best_dir:
                continue
            shutil.rmtree(base_dir+f_dir)


        # setup for next loop
        iter_ct += 1
        change_val *= reduce_amt
        best_paras = dict(pd.read_csv(GAMs_run_dir+'/input_files/parameters.csv', index_col = 0))['Value']
        starting_index = overall_best
        print('next change_val : ', end = '')
        print(change_val)
        print()
        
        
    # save off best parameters to a dictionary
    pickle_in = open('../GAMS/optimization_runs/'+case+'/iter_to_best_run_info.pkl', 'rb')
    iter_to_best_run_info = pickle.load(pickle_in)
    pickle_in.close()
    k = max(iter_to_best_run_info.keys())
    paras_df = pd.read_csv(iter_to_best_run_info[k][2]+'/input_files/parameters.csv', index_col = 0)

    if os.path.exists('../data/interim/misc_dictionaries/case_to_best_paras.pkl'):
        pickle_in = open('../data/interim/misc_dictionaries/case_to_best_paras.pkl', 'rb')
        case_to_best_paras = pickle.load(pickle_in)
        pickle_in.close()
    else:
        case_to_best_paras = {}

    case_to_best_paras.update({case : paras_df})
    pickle_out = open('../data/interim/misc_dictionaries/case_to_best_paras.pkl', 'wb')
    pickle.dump(case_to_best_paras, pickle_out)
    pickle_out.close()
    
    
    # let's remove all but the last iteration to save memory so these can be put on github
    files = os.listdir('../GAMS/optimization_runs/'+case)
    max_file = 'iter_'+str(max([int(f.split('_')[1]) for f in files if 'iter' == f[0:4] and '.pkl' not in f]))
    for f in files:
        if f == max_file:
            continue
        if '.pkl' in f:
            continue
        shutil.rmtree('../GAMS/optimization_runs/'+case+'/'+f)

case not in case_to_best_paras, running with defaults
nan__Arginine: working on iter_ct : 1
running GAMS 27 times...
--- Job combined_model Start 08/01/24 11:17:28 44.1.1 27c4d1f8 LEX-LEG x86 64bit/Linux--- Job combined_model Start 08/01/24 11:17:28 44.1.1 27c4d1f8 LEX-LEG x86 64bit/Linux--- Job combined_model Start 08/01/24 11:17:28 44.1.1 27c4d1f8 LEX-LEG x86 64bit/Linux
--- Applying:

--- Applying:    /opt/gams/gams44.1_linux_x64_64_sfx/gmsprmun.txt
    /opt/gams/gams44.1_linux_x64_64_sfx/gmsprmun.txt

--- GAMS Parameters defined--- Applying:

--- GAMS Parameters defined    Input /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_1/combined_model.gms
    /opt/gams/gams44.1_linux_x64_64_sfx/gmsprmun.txt

    Input /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_3/combined_model.gms    ScrDir /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_1/225a/

    SysDir /opt/gams/gams44.1_linux_x64_64_sfx/    Scr

     21   4        6.4697502448E+01 3.6E+01    32 1.0E+00    7 F  T
     31   4        5.1834329534E+01 4.8E+00    35 1.0E+00    7 T  T
--- combined_model.gms(66) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_0/input_GDX/dimensions.gdx
--- GDX File ($gdxIn) /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_0/input_GDX/dimensions.gdx
--- combined_model.gms(74) 3 Mb
--- call csv2gdx ./input_files/composite_cAct_vals.csv id=cAct index=1,2 values=3..lastCol useHeader=y trace=0 output=./input_GDX/input_cAct.gdx
     36   4        1.0619711019E+02 7.0E-01    35 3.4E+00    2 F  T
     21   4        1.8863141246E+02 3.0E+00    33 4.5E-01    4 F  T

--- combined_model.gms(334) 6 Mb
---   319 rows  358 columns  1,267 non-zeroes
---   9,141 nl-code  945 nl-non-zeroes
--- Range statistics (absolute non-zero finite values)
--- RHS       [min, max] : [        NA,        NA] - Zero values observed as well
--- Bound     [min, max

--- combined_model.gms(359) 4 Mb
--- GDX File (execute_unload) /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_7/output_GDX/act_Kd_metab.gdx
--- combined_model.gms(360) 4 Mb
 
   Iter Phase Ninf     Objective     RGmax    NSB   Step InItr MX OK
     61   4        3.9682147880E+01 6.3E+00    32 1.0E+00    2 F  T
--- combined_model.gms(368) 4 Mb
--- GDX File (execute_unload) /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_4/output_GDX/act_TF_conc.gdx
--- combined_model.gms(369) 4 Mb
--- combined_model.gms(368) 4 Mb
--- GDX File (execute_unload) /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_0/output_GDX/act_TF_conc.gdx
--- combined_model.gms(369) 4 Mb
--- combined_model.gms(362) 4 Mb
--- GDX File (execute_unload) /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_7/output_GDX/inh_Kd_metab.gdx
--- combined_model.gms(363) 4 Mb
*** Status: Normal completion
--- Job combined_mode

--- Job combined_model Start 08/01/24 11:17:29 44.1.1 27c4d1f8 LEX-LEG x86 64bit/Linux
--- Applying:
    /opt/gams/gams44.1_linux_x64_64_sfx/gmsprmun.txt
--- GAMS Parameters defined
    Input /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_8/combined_model.gms
    ScrDir /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_8/225a/
    SysDir /opt/gams/gams44.1_linux_x64_64_sfx/
Licensee: GAMS Community License for Christopher DalldorfG230829|0002AO-GEN
          University of California, San Diego, Bioengineering        CL6627
          /opt/gams/gams44.1_linux_x64_64_sfx/gamslice.txt
          Christopher Dalldorf, cdalldor@eng.ucsd.edu                      
          Community license for demonstration and instructional purposes only
Processor information: 2 socket(s), 12 core(s), and 24 thread(s) available
GAMS 44.1.1   Copyright (C) 1987-2023 GAMS Development. All rights reserved
--- Starting compilation
--- combined_model.gms(65

--- combined_model.gms(105) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_15/input_GDX/input_inh_TF_conc.gdx
--- GDX File ($gdxIn) /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_15/input_GDX/input_inh_TF_conc.gdx
--- combined_model.gms(110) 3 Mb
--- call csv2gdx ./input_files/grid_constants.csv id=basal_constants index=1 values=2..lastCol useHeader=y trace=0 output=./input_GDX/basal.gdx
--- combined_model.gms(141) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_14/input_GDX/max_cInh.gdx
--- GDX File ($gdxIn) /home/chris/github/regulonML/GAMS/optimization_runs/nan__Arginine/iter_1/run_14/input_GDX/max_cInh.gdx
--- combined_model.gms(146) 3 Mb
--- call csv2gdx ./input_files/parameters.csv id=input_parameters index=1 values=2..lastCol useHeader=y trace=0 output=./input_GDX/input_parameters.gdx
--- combined_model.gms(111) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/o

...


--- combined_model.gms(334) 4 Mb 1 Error
*** SOLVE aborted
--- combined_model.gms(334) 4 Mb 1 Error
*** Status: Execution error(s)
--- Job combined_model.gms Stop 08/01/24 11:20:00 elapsed 0:00:00.098
--- combined_model.gms(99) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_14/input_GDX/input_act_TF_conc.gdx
--- GDX File ($gdxIn) /home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_14/input_GDX/input_act_TF_conc.gdx
--- combined_model.gms(104) 3 Mb
--- call csv2gdx ./input_files/exported_inh_TF_conc.csv id=meas_inh_TF index=1 values=2..lastCol useHeader=y trace=0 output=./input_GDX/input_inh_TF_conc.gdx
--- combined_model.gms(99) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_13/input_GDX/input_act_TF_conc.gdx
--- GDX File ($gdxIn) /home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_13/input_GDX/input_act_TF_conc.gdx
--- combined_model.gms(

--- Job combined_model Start 08/01/24 11:20:00 44.1.1 27c4d1f8 LEX-LEG x86 64bit/Linux
--- Applying:
    /opt/gams/gams44.1_linux_x64_64_sfx/gmsprmun.txt
--- GAMS Parameters defined
    Input /home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_16/combined_model.gms
    ScrDir /home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_16/225a/
    SysDir /opt/gams/gams44.1_linux_x64_64_sfx/
Licensee: GAMS Community License for Christopher DalldorfG230829|0002AO-GEN
          University of California, San Diego, Bioengineering        CL6627
          /opt/gams/gams44.1_linux_x64_64_sfx/gamslice.txt
          Christopher Dalldorf, cdalldor@eng.ucsd.edu                      
          Community license for demonstration and instructional purposes only
Processor information: 2 socket(s), 12 core(s), and 24 thread(s) available
GAMS 44.1.1   Copyright (C) 1987-2023 GAMS Development. All rights reserved
--- Starting compilation
--- combined_model.

--- combined_model.gms(87) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_22/input_GDX/input_cInh.gdx
--- GDX File ($gdxIn) /home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_22/input_GDX/input_cInh.gdx
--- combined_model.gms(92) 3 Mb
--- call csv2gdx ./input_files/cInh_mapping.csv id=cInh_mapping index=1 values=2..lastCol useHeader=y trace=0 output=./input_GDX/cInh_mapping.gdx
--- combined_model.gms(111) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_21/input_GDX/basal.gdx
--- GDX File ($gdxIn) /home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_21/input_GDX/basal.gdx
--- combined_model.gms(116) 3 Mb
--- call csv2gdx ./input_files/sample_constants.csv id=sample_constants index=1 values=2..lastCol useHeader=y trace=0 output=./input_GDX/sample_basal.gdx
--- combined_model.gms(93) 3 Mb
--- GDXin=/home/chris/github/regulonML/GAMS/optimization

--- Job combined_model Start 08/01/24 11:20:01 44.1.1 27c4d1f8 LEX-LEG x86 64bit/Linux
--- Applying:
    /opt/gams/gams44.1_linux_x64_64_sfx/gmsprmun.txt
--- GAMS Parameters defined
    Input /home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_25/combined_model.gms
    ScrDir /home/chris/github/regulonML/GAMS/optimization_runs/Fatty_Acid__nan/iter_2/run_25/225a/
    SysDir /opt/gams/gams44.1_linux_x64_64_sfx/
Licensee: GAMS Community License for Christopher DalldorfG230829|0002AO-GEN
          University of California, San Diego, Bioengineering        CL6627
          /opt/gams/gams44.1_linux_x64_64_sfx/gamslice.txt
          Christopher Dalldorf, cdalldor@eng.ucsd.edu                      
          Community license for demonstration and instructional purposes only
Processor information: 2 socket(s), 12 core(s), and 24 thread(s) available
GAMS 44.1.1   Copyright (C) 1987-2023 GAMS Development. All rights reserved
--- Starting compilation--- Job combined_mod

(0, 0, 0)
{'act_TF_conc_lo': 2.902870141566294e-15, 'act_TF_conc_up': 0.0141906595266016, 'act_Kd_lo': 5.6573017297931775e-11, 'act_Kd_up': 1874.0557313797592, 'inh_TF_conc_lo': 2.902870141566294e-15, 'inh_TF_conc_up': 0.0141906595266016, 'inh_Kd_lo': 5.6573017297931775e-11, 'inh_Kd_up': 1874.0557313797592, 'weight_act_obj1': 8.192636589173368, 'weight_inh_obj1': 8.192636589173368, 'weight_mRNA_match': 1.249900724437525e-06, 'inh_metab_Total_lo': 3.8e-14, 'inh_metab_Total_up': 408000.0, 'act_metab_Total_lo': 3.8e-14, 'act_metab_Total_up': 408000.0}
Overall_score: 270000000000.0
cAct_err: 90000000000.0
cInh_err: 90000000000.0
mRNA_err: 90000000000.0


next change_val : 3.2



# save off results

In [38]:
# save off best parameters to a dictionary
for case_iMs in all_cases: # let's get it to work once first
    case = (str(case_iMs[0])+'__'+str(case_iMs[1])).replace('/', '_').replace(' ', '_')
    
    pickle_in = open('../GAMS/optimization_runs/'+case+'/iter_to_best_run_info.pkl', 'rb')
    iter_to_best_run_info = pickle.load(pickle_in)
    pickle_in.close()
    k = max(iter_to_best_run_info.keys())
    paras_df = pd.read_csv(iter_to_best_run_info[k][2]+'/input_files/parameters.csv', index_col = 0)

    if os.path.exists('../data/interim/misc_dictionaries/case_to_best_paras.pkl'):
        pickle_in = open('../data/interim/misc_dictionaries//case_to_best_paras.pkl', 'rb')
        case_to_best_paras = pickle.load(pickle_in)
        pickle_in.close()
    else:
        case_to_best_paras = {}

    case_to_best_paras.update({case : paras_df})
    pickle_out = open('../data/interim/misc_dictionaries//case_to_best_paras.pkl', 'wb')
    pickle.dump(case_to_best_paras, pickle_out)
    pickle_out.close()

In [42]:
# let's remove all but the last iteration to save memory so these can be put on github
for case_iMs in all_cases: # let's get it to work once first
    case = (str(case_iMs[0])+'__'+str(case_iMs[1])).replace('/', '_').replace(' ', '_')
    
    files = os.listdir('../GAMS/optimization_runs/'+case)
    max_file = 'iter_'+str(max([int(f.split('_')[1]) for f in files if 'iter' == f[0:4] and '.pkl' not in f]))
    for f in files:
        if f == max_file:
            continue
        if '.pkl' in f:
            continue
        shutil.rmtree('../GAMS/optimization_runs/'+case+'/'+f)

In [60]:
# copy best results over to the runs
# let's remove all but the last iteration to save memory so these can be put on github
for case_iMs in all_cases: # let's get it to work once first
    case = (str(case_iMs[0])+'__'+str(case_iMs[1])).replace('/', '_').replace(' ', '_')
    
    files = os.listdir('../GAMS/optimization_runs/'+case)
    max_file = 'iter_'+str(max([int(f.split('_')[1]) for f in files if 'iter' == f[0:4] and '.pkl' not in f]))
    files2 = os.listdir('../GAMS/optimization_runs/'+case+'/'+max_file)
    max_run = 'run_'+str(max([int(f.split('_')[1]) for f in files2 if 'run_' == f[0:4] and '.pkl' not in f]))
    if os.path.exists('../GAMS/runs/'+case):
        shutil.rmtree('../GAMS/runs/'+case)
    os.mkdir('../GAMS/runs/'+case)
    copy_tree('../GAMS/optimization_runs/'+case+'/'+max_file+'/'+max_run, '../GAMS/runs/'+case)